In [1]:
#Importing libraries
import torch
import torch.nn as nn
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
from torch.autograd import Variable
%matplotlib inline
from sklearn.metrics import classification_report, confusion_matrix, accuracy_score
from sklearn.preprocessing import StandardScaler
from sklearn.decomposition import PCA
from sklearn.linear_model import LogisticRegression

np.random.seed(1234)
torch.manual_seed(1234)

#Reading data
learn_data = pd.read_csv("churn_modelling_audience.csv")
pd.options.display.max_columns = None
learn_data

In [2]:
#Reading data
learn_data = pd.read_csv("churn_modelling_audience.csv")
pd.options.display.max_columns = None
learn_data

id last_order_city_name customer_type  \
0      20002006408704             İstanbul    INDIVIDUAL   
1      20002005920692               Artvin    INDIVIDUAL   
2      20002001678732                İzmir    INDIVIDUAL   
3      20002002795327                Hatay    INDIVIDUAL   
4      20002006408404                Bursa    INDIVIDUAL   
...               ...                  ...           ...   
15995  20002003647460               Ankara    INDIVIDUAL   
15996  20002009472837               Ankara    INDIVIDUAL   
15997  20002009066319               Ankara    INDIVIDUAL   
15998  20002003401739               Ankara    INDIVIDUAL   
15999  20002006185654                Muğla    INDIVIDUAL   

      last_order_device_channel  days_from_last_order  days_from_last_seen_at  \
0                       BROWSER                   149                     125   
1                       BROWSER                   190                      58   
2                           APP                    89                      88   
3                           APP                   162                      58   
4                       BROWSER                   149                      89   
...                         ...                   ...                     ...   
15995                   BROWSER                   358                     264   
15996                       APP                    46                      46   
15997                       APP                    78                      15   
15998                       APP                   341                     170   
15999                       APP                    50                      15   

       lifetime_order_count  last30_days_order_amount  \
0                         1                         0   
1                         1                         0   
2                         1                         0   
3                         1                         0   
4                         1                         0   
...                     ...                       ...   
15995                     3                         0   
15996                     1                         0   
15997                     1                         0   
15998                     5                         0   
15999                    10                         0   

       last30_days_order_count  last90_days_order_amount  \
0                            0                         0   
1                            0                         0   
2                            0                      6086   
3                            0                         0   
4                            0                         0   
...                        ...                       ...   
15995                        0                         0   
15996                        0                      6058   
15997                        0                     11934   
15998                        0                         0   
15999                        0                     48481   

       last90_days_order_count  last365_days_order_amount  \
0                            0                       6375   
1                            0                      18435   
2                            1                       6086   
3                            0                      10615   
4                            0                      15186   
...                        ...                        ...   
15995                        0                      26996   
15996                        1                       6058   
15997                        1                      11934   
15998                        0                      37651   
15999                        2                     189641   

       last365_days_order_count  churn  
0                             1   True  
1                             1   True  
2                             1  False  
3                     

In [3]:
#Defining columns
numerical_columns = ['days_from_last_order', 'days_from_last_seen_at', 'lifetime_order_count',
                     'last30_days_order_amount', 'last30_days_order_count','last90_days_order_amount','last90_days_order_count','last365_days_order_amount','last365_days_order_count']

categorical_columns = ['last_order_city_name', 'customer_type', 'last_order_device_channel']
outputs = ['churn']

In [4]:
churn_data = learn_data[learn_data['churn'] == 'True']
notchurn_data = learn_data[learn_data['churn'] == 'False']

In [5]:
#Processing columns

#Numerical
numerical_data = np.stack([learn_data[col].values for col in numerical_columns], 1)
numerical_data = torch.tensor(numerical_data, dtype=torch.float)

#Categorical
for category in categorical_columns:
    learn_data[category] = learn_data[category].astype('category')
    
cn = learn_data['last_order_city_name'].cat.codes.values
ct = learn_data['customer_type'].cat.codes.values
dc = learn_data['last_order_device_channel'].cat.codes.values

categorical_data = np.stack([cn,ct,dc], 1)
categorical_data = torch.tensor(categorical_data, dtype=torch.int64)

#Outputs
learn_data[outputs] = learn_data[outputs].astype(int)

outputs = torch.tensor(learn_data[outputs].values).flatten()
outputs = outputs.long()

In [6]:
#Dividing the data
total_records = 16000
train_records = int(total_records * .6)
valid_records = int(total_records * .2)
test_records = int(total_records * .2)
numerical_train_data = numerical_data[:train_records]
numerical_valid_data = numerical_data[train_records:train_records+valid_records]
numerical_test_data = numerical_data[train_records+valid_records:total_records]
categorical_train_data = categorical_data[:train_records]
categorical_valid_data = categorical_data[train_records:train_records+valid_records]
categorical_test_data = categorical_data[train_records+valid_records:total_records]
train_outputs = outputs[:train_records]
valid_outputs = outputs[train_records:train_records+valid_records]
test_outputs = outputs[train_records+valid_records:total_records]

In [7]:
from torch.nn.parameter import Parameter
from torch.nn import init
import math

#Creating the Neural Network
class Model(nn.Module):

    def __init__(self):
        super().__init__()
        self.layer1 = nn.Linear(9, 100)
        self.relu = nn.ReLU(inplace=True)
        self.bn1 = nn.BatchNorm1d(100)
        self.weights1 = Parameter(torch.Tensor(1, 115))
        init.kaiming_uniform_(self.weights1, a=math.sqrt(5))
        
        self.weights2 = Parameter(torch.Tensor(1, 115))
        init.kaiming_uniform_(self.weights2, a=math.sqrt(5))
        
        self.bias1 = Parameter(torch.Tensor(1))
        fan_in, _ = init._calculate_fan_in_and_fan_out(self.weights1)
        bound = 1 / math.sqrt(fan_in)
        init.uniform_(self.bias1, -bound, bound)
        
        self.bias2 = Parameter(torch.Tensor(1))
        fan_in, _ = init._calculate_fan_in_and_fan_out(self.weights2)
        bound = 1 / math.sqrt(fan_in)
        init.uniform_(self.bias2, -bound, bound)
        
        self.layer1_1 = nn.Embedding(81, 5)
        self.bn1_1 = nn.BatchNorm1d(5)
        self.layer1_2 = nn.Embedding(4, 5)
        self.bn1_2 = nn.BatchNorm1d(5)
        self.layer1_3 = nn.Embedding(3, 5)
        self.bn1_3 = nn.BatchNorm1d(5)
        
        self.layer2 = nn.Linear(115, 115)
        self.bn2 = nn.BatchNorm1d(115)
        
    def forward(self, x_numerical, x_categorical):
        x1 = self.layer1(x_numerical)
        x1 = self.relu(x1)
        x1 = self.bn1(x1)
        
        x1_embedding = self.layer1_1(x_categorical[:,0])
        x1_embedding = self.relu(x1_embedding)
        x1_embedding = self.bn1_1(x1_embedding)
        
        x2_embedding = self.layer1_2(x_categorical[:,1])
        x2_embedding = self.relu(x2_embedding)
        x2_embedding = self.bn1_2(x2_embedding)
        
        x3_embedding = self.layer1_3(x_categorical[:,2])
        x3_embedding = self.relu(x3_embedding)
        x3_embedding = self.bn1_3(x3_embedding)
        
        x_embedding = torch.cat([x1_embedding,x2_embedding,x3_embedding], 1)
                
        x1 = torch.cat([x1, x_embedding], 1)
        
        x2 = self.layer2(x1)        
        emb = self.relu(x2)
        x2 = self.bn2(emb)
        
        
        x2_weights1 = torch.mm(x2, self.weights1.t()) + self.bias1
        x2_weights2 = torch.mm(x2, self.weights2.t()) + self.bias2
        
        x3 = torch.cat([x2_weights1, x2_weights2], 1)
        
                
        return emb, self.weights1, self.weights2, x3

In [8]:
model = Model()

In [9]:
#===============================================================================================
# Defining churn:loyal weight ratio. churn_percentage=0.7 means churn:loyal weight ratio of 7:3.
# Setting churn_percentage=0.5 to get an unweighted model
#===============================================================================================
churn_percentage = 0.7

#Defining loss function
loss_function = nn.CrossEntropyLoss(weight=torch.Tensor([1-churn_percentage, churn_percentage]))
# loss_function = nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(model.parameters(), lr=0.001)
#29 Juni 2020: menambahkan scheduler learning rate
scheduler = torch.optim.lr_scheduler.ExponentialLR(optimizer, 0.9)

In [10]:
#Training the data
epochs = 100 
batch_size = 10
mean_losses_train = []
mean_losses_valid = []
best_loss_valid = np.inf

for i in range(epochs):
    model.train()
    aggregated_losses_train = []
    aggregated_losses_valid = []
    i += 1
    idxs = np.random.permutation(train_records)
    for j in range((train_records//batch_size)+1):
        start_train = j*batch_size
        end_train = start_train+batch_size
        
        idxs_batch = idxs[start_train:end_train]
        
        train, weights1, weights2, train_embed = model(numerical_train_data[idxs_batch], categorical_train_data[idxs_batch]) # yg error 1
        train_loss = loss_function(train_embed, train_outputs[idxs_batch])
        aggregated_losses_train.append(train_loss)

        print(f'iteration: {j:3} loss: {train_loss.item():10.8f}')

        optimizer.zero_grad()
        train_loss.backward()
        optimizer.step()
        mean_loss_train = torch.mean(torch.stack(aggregated_losses_train))
        
    print(f'epoch: {i:3} mean loss training: {mean_loss_train.item():10.8f}')
    mean_losses_train.append(mean_loss_train)
    
    model.eval()
    with torch.set_grad_enabled(False):
        for k in range((valid_records//batch_size)+1):
            start_valid = k*batch_size
            end_valid = start_valid+batch_size
            valid, weights1, weights2, valid_embed = model(numerical_valid_data[start_valid:end_valid], categorical_valid_data[start_valid:end_valid]) # kenapa disini harus ada 2 variabel prefix
            valid_loss = loss_function(valid_embed, valid_outputs[start_valid:end_valid])
            aggregated_losses_valid.append(valid_loss)
    mean_loss_valid = torch.mean(torch.stack(aggregated_losses_valid))
    print(f'epoch: {i:3} mean loss validation: {mean_loss_valid:.8f}')
    
    if mean_loss_valid.cpu().numpy()[()] < best_loss_valid:
        best_loss_valid = mean_loss_valid
        torch.save(model.state_dict(), "model_train_cre_{}.pth".format(churn_percentage))
        best_epoch = i        
    
    mean_losses_valid.append(mean_loss_valid)
    scheduler.step()

iteration:   0 loss: 0.64676756
iteration:   1 loss: 0.73016751
iteration:   2 loss: 0.62819940
iteration:   3 loss: 0.53813386
iteration:   4 loss: 0.54768616
iteration:   5 loss: 0.45143563
iteration:   6 loss: 0.31186455
iteration:   7 loss: 0.27859604
iteration:   8 loss: 0.95706284
iteration:   9 loss: 0.38139245
iteration:  10 loss: 0.68314958
iteration:  11 loss: 1.10004640
iteration:  12 loss: 0.70261395
iteration:  13 loss: 0.35743389
iteration:  14 loss: 0.52798635
iteration:  15 loss: 0.22729336
iteration:  16 loss: 0.37136981
iteration:  17 loss: 0.13433753
iteration:  18 loss: 0.56490171
iteration:  19 loss: 0.22121730
iteration:  20 loss: 0.24083303
iteration:  21 loss: 0.47505936
iteration:  22 loss: 0.31072843
iteration:  23 loss: 0.19871701
iteration:  24 loss: 0.31982553
iteration:  25 loss: 0.28671351
iteration:  26 loss: 0.18316855
iteration:  27 loss: 0.18284267
iteration:  28 loss: 0.56521499
iteration:  29 loss: 0.14901242
iteration:  30 loss: 0.25649658
iteratio

iteration: 263 loss: 0.20005217
iteration: 264 loss: 0.40746132
iteration: 265 loss: 0.17386235
iteration: 266 loss: 0.18479620
iteration: 267 loss: 0.03457800
iteration: 268 loss: 0.07120296
iteration: 269 loss: 0.03577852
iteration: 270 loss: 0.08358262
iteration: 271 loss: 0.12822689
iteration: 272 loss: 0.56366605
iteration: 273 loss: 0.33761299
iteration: 274 loss: 0.08098362
iteration: 275 loss: 1.53040123
iteration: 276 loss: 0.16198660
iteration: 277 loss: 0.07440978
iteration: 278 loss: 0.17879668
iteration: 279 loss: 0.05656803
iteration: 280 loss: 0.28459224
iteration: 281 loss: 0.12639411
iteration: 282 loss: 0.26426983
iteration: 283 loss: 0.14851700
iteration: 284 loss: 0.24873093
iteration: 285 loss: 0.02568336
iteration: 286 loss: 0.47827512
iteration: 287 loss: 0.02633753
iteration: 288 loss: 0.63936663
iteration: 289 loss: 0.04891144
iteration: 290 loss: 0.11757700
iteration: 291 loss: 0.14842550
iteration: 292 loss: 0.14951172
iteration: 293 loss: 0.09001678
iteratio

iteration: 557 loss: 0.04555017
iteration: 558 loss: 0.23879625
iteration: 559 loss: 0.21569057
iteration: 560 loss: 0.20985420
iteration: 561 loss: 0.73910177
iteration: 562 loss: 0.25315061
iteration: 563 loss: 0.06171339
iteration: 564 loss: 0.17661841
iteration: 565 loss: 0.28836241
iteration: 566 loss: 0.61767393
iteration: 567 loss: 0.50787860
iteration: 568 loss: 0.06789719
iteration: 569 loss: 0.16812274
iteration: 570 loss: 0.15182105
iteration: 571 loss: 0.10915531
iteration: 572 loss: 0.34361625
iteration: 573 loss: 0.06257208
iteration: 574 loss: 0.01893676
iteration: 575 loss: 0.26378527
iteration: 576 loss: 0.06276723
iteration: 577 loss: 0.03856051
iteration: 578 loss: 0.09628273
iteration: 579 loss: 0.74246716
iteration: 580 loss: 0.03389280
iteration: 581 loss: 0.03365352
iteration: 582 loss: 0.08118773
iteration: 583 loss: 0.05949713
iteration: 584 loss: 0.33540341
iteration: 585 loss: 0.14340341
iteration: 586 loss: 0.22973025
iteration: 587 loss: 0.53680509
iteratio

iteration: 816 loss: 0.02294156
iteration: 817 loss: 0.06632848
iteration: 818 loss: 0.01636500
iteration: 819 loss: 0.16046292
iteration: 820 loss: 0.77938974
iteration: 821 loss: 0.29743409
iteration: 822 loss: 0.02495072
iteration: 823 loss: 0.18074480
iteration: 824 loss: 0.10811836
iteration: 825 loss: 1.24630773
iteration: 826 loss: 0.23829806
iteration: 827 loss: 0.04905530
iteration: 828 loss: 0.20903993
iteration: 829 loss: 0.25404736
iteration: 830 loss: 0.04948591
iteration: 831 loss: 0.51739484
iteration: 832 loss: 0.21830437
iteration: 833 loss: 0.02791900
iteration: 834 loss: 0.14531530
iteration: 835 loss: 0.51486284
iteration: 836 loss: 0.02728893
iteration: 837 loss: 0.33351111
iteration: 838 loss: 0.04771028
iteration: 839 loss: 0.73848069
iteration: 840 loss: 0.15668535
iteration: 841 loss: 0.03837992
iteration: 842 loss: 0.33164001
iteration: 843 loss: 0.17868543
iteration: 844 loss: 0.02056045
iteration: 845 loss: 0.27145055
iteration: 846 loss: 0.33468789
iteratio

iteration: 156 loss: 0.04921964
iteration: 157 loss: 0.06067132
iteration: 158 loss: 0.09212440
iteration: 159 loss: 0.05661419
iteration: 160 loss: 0.01800955
iteration: 161 loss: 0.17843750
iteration: 162 loss: 0.12232161
iteration: 163 loss: 0.02692310
iteration: 164 loss: 0.02168740
iteration: 165 loss: 0.03006400
iteration: 166 loss: 0.01891127
iteration: 167 loss: 0.35116124
iteration: 168 loss: 0.35253876
iteration: 169 loss: 0.04612173
iteration: 170 loss: 0.04609128
iteration: 171 loss: 0.08340320
iteration: 172 loss: 0.02023463
iteration: 173 loss: 0.06712083
iteration: 174 loss: 0.02846364
iteration: 175 loss: 0.23867081
iteration: 176 loss: 0.08780582
iteration: 177 loss: 0.01282612
iteration: 178 loss: 0.18597485
iteration: 179 loss: 0.14717089
iteration: 180 loss: 0.40721306
iteration: 181 loss: 0.03223279
iteration: 182 loss: 0.14198084
iteration: 183 loss: 0.10330637
iteration: 184 loss: 0.03599973
iteration: 185 loss: 0.02433227
iteration: 186 loss: 0.13128443
iteratio

...

iteration: 691 loss: 0.00726376
iteration: 692 loss: 0.00308691
iteration: 693 loss: 0.07815087
iteration: 694 loss: 0.04515772
iteration: 695 loss: 0.03915105
iteration: 696 loss: 0.06703589
iteration: 697 loss: 0.12683186
iteration: 698 loss: 0.08743995
iteration: 699 loss: 0.01117971
iteration: 700 loss: 0.09741374
iteration: 701 loss: 0.08113458
iteration: 702 loss: 0.08891249
iteration: 703 loss: 0.01083271
iteration: 704 loss: 0.47254199
iteration: 705 loss: 0.08834864
iteration: 706 loss: 0.02952575
iteration: 707 loss: 0.01074417
iteration: 708 loss: 0.22522141
iteration: 709 loss: 0.11790583
iteration: 710 loss: 0.02010229
iteration: 711 loss: 0.22250809
iteration: 712 loss: 0.02766487
iteration: 713 loss: 0.04853685
iteration: 714 loss: 0.21772416
iteration: 715 loss: 0.01010690
iteration: 716 loss: 0.08470747
iteration: 717 loss: 0.15271372
iteration: 718 loss: 0.00531203
iteration: 719 loss: 0.17153546
iteration: 720 loss: 0.06633546
iteration: 721 loss: 0.01975547
iteratio

iteration: 953 loss: 0.09526481
iteration: 954 loss: 0.05425753
iteration: 955 loss: 0.06658421
iteration: 956 loss: 0.00729373
iteration: 957 loss: 0.02281914
iteration: 958 loss: 0.18809570
iteration: 959 loss: 0.10445518
iteration: 960 loss:        nan
epoch:  99 mean loss training:        nan
epoch:  99 mean loss validation: nan
iteration:   0 loss: 0.01143360
iteration:   1 loss: 0.01489968
iteration:   2 loss: 0.10420816
iteration:   3 loss: 0.12947524
iteration:   4 loss: 0.02042906
iteration:   5 loss: 0.11575129
iteration:   6 loss: 0.05284653
iteration:   7 loss: 0.00667785
iteration:   8 loss: 0.01608761
iteration:   9 loss: 0.03728197
iteration:  10 loss: 0.10482130
iteration:  11 loss: 0.00705460
iteration:  12 loss: 0.10984890
iteration:  13 loss: 0.12691179
iteration:  14 loss: 0.02183123
iteration:  15 loss: 0.00942488
iteration:  16 loss: 0.01213496
iteration:  17 loss: 0.00506712
iteration:  18 loss: 0.11117947
iteration:  19 loss: 0.00984199
iteration:  20 loss: 0.22

iteration: 287 loss: 0.21182762
iteration: 288 loss: 0.04038684
iteration: 289 loss: 0.11494369
iteration: 290 loss: 0.03654205
iteration: 291 loss: 0.02538478
iteration: 292 loss: 0.01659815
iteration: 293 loss: 0.00877637
iteration: 294 loss: 0.01875685
iteration: 295 loss: 0.08660014
iteration: 296 loss: 0.02689983
iteration: 297 loss: 0.01196883
iteration: 298 loss: 0.04684705
iteration: 299 loss: 0.67318082
iteration: 300 loss: 0.15298717
iteration: 301 loss: 0.19778548
iteration: 302 loss: 0.19848193
iteration: 303 loss: 0.06756171
iteration: 304 loss: 0.05896638
iteration: 305 loss: 0.12346079
iteration: 306 loss: 0.04860086
iteration: 307 loss: 0.04930926
iteration: 308 loss: 0.00728453
iteration: 309 loss: 0.00747897
iteration: 310 loss: 0.00967852
iteration: 311 loss: 0.12244093
iteration: 312 loss: 0.00812309
iteration: 313 loss: 0.11975234
iteration: 314 loss: 0.14154449
iteration: 315 loss: 0.03756903
iteration: 316 loss: 0.25036564
iteration: 317 loss: 0.20316280
iteratio

iteration: 580 loss: 0.17117576
iteration: 581 loss: 0.04842520
iteration: 582 loss: 0.01841153
iteration: 583 loss: 0.01405576
iteration: 584 loss: 0.02045159
iteration: 585 loss: 0.19907162
iteration: 586 loss: 0.01000643
iteration: 587 loss: 0.02110123
iteration: 588 loss: 0.06792379
iteration: 589 loss: 0.01569155
iteration: 590 loss: 0.03715961
iteration: 591 loss: 0.09211117
iteration: 592 loss: 0.20007777
iteration: 593 loss: 0.08472876
iteration: 594 loss: 0.02534883
iteration: 595 loss: 0.02392639
iteration: 596 loss: 0.02234812
iteration: 597 loss: 0.01065751
iteration: 598 loss: 0.00725645
iteration: 599 loss: 0.02250678
iteration: 600 loss: 0.44953373
iteration: 601 loss: 0.11765365
iteration: 602 loss: 0.09086029
iteration: 603 loss: 0.05896073
iteration: 604 loss: 0.01920528
iteration: 605 loss: 0.12779947
iteration: 606 loss: 0.00882563
iteration: 607 loss: 0.06087462
iteration: 608 loss: 0.01760896
iteration: 609 loss: 0.11040738
iteration: 610 loss: 0.12121888
iteratio

iteration: 850 loss: 0.16860498
iteration: 851 loss: 0.03213175
iteration: 852 loss: 0.04130978
iteration: 853 loss: 0.03579464
iteration: 854 loss: 0.00869907
iteration: 855 loss: 0.00932485
iteration: 856 loss: 0.22650306
iteration: 857 loss: 0.01441751
iteration: 858 loss: 0.22651179
iteration: 859 loss: 0.34612051
iteration: 860 loss: 0.08144560
iteration: 861 loss: 0.11048730
iteration: 862 loss: 0.03339070
iteration: 863 loss: 0.01417683
iteration: 864 loss: 0.13702191
iteration: 865 loss: 0.00514945
iteration: 866 loss: 0.05342191
iteration: 867 loss: 0.03114168
iteration: 868 loss: 0.06750426
iteration: 869 loss: 0.05023440
iteration: 870 loss: 0.07886650
iteration: 871 loss: 0.08465657
iteration: 872 loss: 0.02324163
iteration: 873 loss: 0.00798587
iteration: 874 loss: 0.04887370
iteration: 875 loss: 0.00582654
iteration: 876 loss: 0.40207946
iteration: 877 loss: 0.25923935
iteration: 878 loss: 0.01839584
iteration: 879 loss: 0.01074700
iteration: 880 loss: 0.09491438
iteratio

In [11]:
model.load_state_dict(torch.load("model_train_cre_{}.pth".format(churn_percentage)))

FileNotFoundError: [Errno 2] No such file or directory: 'model_train_cre_0.7.pth'

In [ ]:
#Creating predictions
with torch.no_grad():
    valid, valid_weights1, valid_weights2, valid_embed = model(numerical_valid_data, categorical_valid_data)
    valid_loss = loss_function(valid_embed, valid_outputs)
    total_valid_loss = valid_loss
print(f'Loss: {total_valid_loss:.8f}')

In [ ]:
# =============================================================================================
# [26 Mei 2020]: 
# hasil utama yang dilihat adalah F1 Score, karena metrik akurasi misleading digunakan untuk 
# data imbalance
# =============================================================================================

from sklearn.metrics import f1_score

valid_val = np.argmax(valid_embed, axis=1)
print(confusion_matrix(valid_outputs, valid_val))
print(classification_report(valid_outputs, valid_val))
print("Accuracy: ", accuracy_score(valid_outputs, valid_val))
print("F1 Score: ", f1_score(valid_outputs, valid_val, average='macro'))

In [ ]:
# function for smoothing the loss plot by using exponential moving average
# https://stackoverflow.com/questions/42281844/what-is-the-mathematics-behind-the-smoothing-parameter-in-tensorboards-scalar
def smooth(scalars, weight):
    last = scalars[0]  # First value in the plot (first timestep)
    smoothed = list()
    for point in scalars:
        smoothed_val = last * weight + (1 - weight) * point  # Calculate smoothed value
        smoothed.append(smoothed_val)                        # Save it
        last = smoothed_val                                  # Anchor the last smoothed value

    return smoothed

In [ ]:
epochs_to_show = 100
smoothing = 0.5
plt.figure(figsize=(10,5))
plt.plot(range(1,epochs_to_show+1), smooth(mean_losses_train[0:epochs_to_show],smoothing), label = 'train')
plt.plot(range(1,epochs_to_show+1), smooth(mean_losses_valid[0:epochs_to_show],smoothing), label = 'validation')
plt.xlabel('epochs')
plt.ylabel('loss')
plt.legend(loc='upper right')
# plt.ylim((0.0, 0.9))
# plt.title('loss graph')
plt.show()
print(best_epoch)